# Import Library

In [190]:
import pickle
import pandas as pd
import util
import numpy as np
import matplotlib.pyplot as plt
pd.options.plotting.backend = "plotly"

# Load models

In [93]:
model_rf_reg = pickle.load(open('./saved_model/rf_reg.pkl', "rb"))
model_xgb_reg = pickle.load(open('./saved_model/xgb_reg.pkl', "rb"))
model_autokeras_reg = pickle.load(open('./saved_model/autokeras_reg.pkl', "rb"))


# Setup data

In [94]:
dataset = pd.read_csv('./data_train\df_raw.csv')
dataset.index = dataset.time
dataset =dataset.drop(['time'],axis=1)
dfs = util.df_group_by_col(df=dataset, col='deviceId')
dataset = dfs[0].drop(['deviceId'],axis=1)
dataset['target'] = dataset['co2'].shift(-15)
dataset = dataset[:-15]
dataset_numeric = dataset
dataset_numeric

temperature          co2    iaq       target
time                                                                   
2022-11-07 23:15:18+11:00    24.787203  1063.735229  179.0  1042.386719
2022-11-07 23:16:18+11:00    24.782167  1056.472656  177.0  1056.373047
2022-11-07 23:17:18+11:00    24.789717  1065.587769  179.0  1062.436279
2022-11-07 23:18:18+11:00    24.784685  1064.388428  179.0  1049.018311
2022-11-07 23:19:18+11:00    24.792234  1063.462036  178.0  1053.749268
...                                ...          ...    ...          ...
2022-11-11 13:41:08+11:00    24.736872   613.454834   57.0   646.477234
2022-11-11 13:42:08+11:00    24.754488   615.277893   58.0   645.051270
2022-11-11 13:43:08+11:00    24.714224   636.333313   70.0   653.881470
2022-11-11 13:44:08+11:00    24.678993   647.243347   77.0   669.776306
2022-11-11 13:45:08+11:00    24.671442   649.089966   78.0   705.225464

[4788 rows x 4 columns]

# Data scaling

In [95]:
max_d = dataset_numeric['target'].max()
min_d = dataset_numeric['target'].min()
#denormalized_d = normalized_d * (max_d - min_d) + min_d
print(max_d, min_d)

dataset_scaled =(dataset_numeric-dataset_numeric.min())/(dataset_numeric.max()-dataset_numeric.min())
dataset_scaled

1353.922607421875 602.8489379882812


temperature       co2       iaq    target
time                                                                
2022-11-07 23:15:18+11:00     0.522236  0.613637  0.842105  0.585213
2022-11-07 23:16:18+11:00     0.519366  0.603967  0.828947  0.603834
2022-11-07 23:17:18+11:00     0.523670  0.616103  0.842105  0.611907
2022-11-07 23:18:18+11:00     0.520801  0.614506  0.842105  0.594042
2022-11-07 23:19:18+11:00     0.525105  0.613273  0.835526  0.600341
...                                ...       ...       ...       ...
2022-11-11 13:41:08+11:00     0.493541  0.014121  0.039474  0.058088
2022-11-11 13:42:08+11:00     0.503585  0.016548  0.046053  0.056189
2022-11-11 13:43:08+11:00     0.480629  0.044582  0.125000  0.067946
2022-11-11 13:44:08+11:00     0.460543  0.059108  0.171053  0.089109
2022-11-11 13:45:08+11:00     0.456238  0.061567  0.177632  0.136307

[4788 rows x 4 columns]

# Create lookback dataset

In [96]:
lookback = 60

features = list(dataset_scaled.drop(['target'],axis=1).columns)
dataset_lb = dataset_scaled[:]

for i in range(1,lookback):    
    features_lb = list(map(lambda ls: ls+"_"+str(i), features))
    dataset_lb[features_lb]= dataset_scaled.drop(['target'],axis=1).shift(i)

dataset_lb = dataset_lb[lookback:]
dataset_lb
dataset = dataset_lb
dataset

C:\Users\ANPCC\AppData\Local\Temp\ipykernel_19440\223088852.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataset_lb[features_lb]= dataset_scaled.drop(['target'],axis=1).shift(i)
C:\Users\ANPCC\AppData\Local\Temp\ipykernel_19440\223088852.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataset_lb[features_lb]= dataset_scaled.drop(['target'],axis=1).shift(i)
C:\Users\ANPCC\AppData\Local\Temp\ipykernel_19440\223088852.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fr

temperature       co2       iaq    target  \
time                                                                   
2022-11-08 00:15:18+11:00     0.487803  0.589232  0.809211  0.551340   
2022-11-08 00:16:18+11:00     0.479212  0.582024  0.802632  0.582618   
2022-11-08 00:17:18+11:00     0.479194  0.587984  0.809211  0.581631   
2022-11-08 00:18:18+11:00     0.477759  0.582083  0.802632  0.588554   
2022-11-08 00:19:18+11:00     0.479212  0.582584  0.802632  0.578412   
...                                ...       ...       ...       ...   
2022-11-11 13:41:08+11:00     0.493541  0.014121  0.039474  0.058088   
2022-11-11 13:42:08+11:00     0.503585  0.016548  0.046053  0.056189   
2022-11-11 13:43:08+11:00     0.480629  0.044582  0.125000  0.067946   
2022-11-11 13:44:08+11:00     0.460543  0.059108  0.171053  0.089109   
2022-11-11 13:45:08+11:00     0.456238  0.061567  0.177632  0.136307   

                           temperature_1     co2_1     iaq_1  temperature_2  \
time                                                                          
2022-11-08 00:15:18+11:00       0.487803  0.588067  0.809211       0.484933   
2022-11-08 00:16:18+11:00       0.487803  0.589232  0.809211       0.487803   
2022-11-08 00:17:18+11:00       0.479212  0.582024  0.802632       0.487803   
2022-11-08 00:18:18+11:00       0.479194  0.587984  0.809211       0.479212   
2022-11-08 00:19:18+11:00       0.477759  0.582083  0.802632       0.479194   
...                                  ...       ...       ...            ...   
2022-11-11 13:41:08+11:00       0.490671  0.013907  0.039474       0.476325   
2022-11-11 13:42:08+11:00       0.493541  0.014121  0.039474       0.490671   
2022-11-11 13:43:08+11:00       0.503585  0.016548  0.046053       0.493541   
2022-11-11 13:44:08+11:00       0.480629  0.044582  0.125000       0.503585   
2022-11-11 13:45:08+11:00       0.460543  0.059108  0.171053       0.480629   

                              co2_2     iaq_2  ...    iaq_56  temperature_57  \
time                                           ...                             
2022-11-08 00:15:18+11:00  0.588588  0.809211  ...  0.835526        0.520801   
2022-11-08 00:16:18+11:00  0.588067  0.809211  ...  0.835526        0.525105   
2022-11-08 00:17:18+11:00  0.589232  0.809211  ...  0.835526        0.519366   
2022-11-08 00:18:18+11:00  0.582024  0.802632  ...  0.835526        0.516497   
2022-11-08 00:19:18+11:00  0.587984  0.809211  ...  0.835526        0.510757   
...                             ...       ...  ...       ...             ...   
2022-11-11 13:41:08+11:00  0.013700  0.039474  ...  0.092105        0.407459   
2022-11-11 13:42:08+11:00  0.013907  0.039474  ...  0.078947        0.408892   
2022-11-11 13:43:08+11:00  0.014121  0.039474  ...  0.085526        0.408892   
2022-11-11 13:44:08+11:00  0.016548  0.046053  ...  0.085526        0.406023   
2022-11-11 13:45:08+11:00  0.044582  0.125000  ...  0.092105        0.407459   

                             co2_57    iaq_57  temperature_58    co2_58  \
time                                                                      
2022-11-08 00:15:18+11:00  0.614506  0.842105        0.523670  0.616103   
2022-11-08 00:16:18+11:00  0.613273  0.835526        0.520801  0.614506   
2022-11-08 00:17:18+11:00  0.609991  0.835526        0.525105  0.613273   
2022-11-08 00:18:18+11:00  0.612629  0.835526        0.519366  0.609991   
2022-11-08 00:19:18+11:00  0.610349  0.835526        0.516497  0.612629   
...                             ...       ...             ...       ...   
2022-11-11 13:41:08+11:00  0.032102  0.092105        0.406023  0.034517   
2022-11-11 13:42:08+11:00  0.031365  0.092105        0.407459  0.032102   
2022-11-11 13:43:08+11:00  0.026473  0.078947        0.408892  0.031365   
2022-11-11 13:44:08+11:00  0.030624  0.085526        0.408892  0.026473   
2022-11-11 13:45:08+11:00  0.031033  0.085526        0.406023  0.030624   

                             iaq_58  temperat

# Split target and data

In [97]:
data =dataset.drop(['target'],axis=1)
target = dataset['target']

# Bandit arm setup

In [177]:
models =[model_rf_reg, model_xgb_reg, model_autokeras_reg]

# bandit setting
arms ={
        0:model_rf_reg, 
        1:model_xgb_reg, 
        #2:model_autokeras_reg, 
      }
#scores_ucb1={0:5,1:5,2:5}
#arms_name = ['model_rf_reg','model_xgb_reg','model_autokeras_reg']
scores={0:3,1:5}
arms_name = ['model_rf_reg','model_xgb_reg']

# UCB1 bandit algorithm 

In [200]:
history = pd.DataFrame(data=None, columns=['time','action','prediction','reward','explore','score','count','score_ucb1'])
y_history= []
hisplot = pd.DataFrame(data=None, columns= arms_name)

for i in range(len(data)):
    
    action = max(scores, key= lambda x: scores[x])
    #print(action)
    data_1step = data[i:i+1]
    y_true = target[i:i+1]
    y_pred = arms[action].predict(data_1step)

    loss_avg = np.mean(abs(y_true- y_pred)) # average loss is the reward here
    reward = np.exp(-loss_avg)

    y_pred_iv = y_pred* (max_d - min_d) + min_d
    y_test_iv = y_true* (max_d - min_d) + min_d
    loss_iv = abs(y_pred_iv-y_test_iv)   
    
    history.loc[i]=[i,action,y_pred[0],reward,'explore',None,None,None]
    score = history[['action', 'reward']].groupby('action').agg({'reward': ['mean', 'count']})
    
    ubc1_arr = [] 
    for actionX in range(len(scores)):
        try:
            mu, ct = score.loc[actionX]

            history['score'].loc[i] = mu
            history['count'].loc[i] = ct

            ucb1 = mu + np.sqrt((2*np.log10(i+1))/ct)

            scores[actionX] = ucb1
            ubc1_arr.append(ucb1)
            
        except:
            ubc1_arr.append(0)

    history['score_ucb1'][i] = ubc1_arr
    history['time'][i] = data_1step.index.values
    y_history.append(y_pred[0])

    hisplot.loc[i, arms_name[action]] = y_pred_iv
    
display(history)
print(scores) 


C:\Users\ANPCC\AppData\Local\Temp\ipykernel_19440\3149693550.py:28: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ANPCC\AppData\Local\Temp\ipykernel_19440\3149693550.py:29: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ANPCC\AppData\Local\Temp\ipykernel_19440\3149693550.py:39: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ANPCC\AppData\Local\Temp\ipykernel_19440\3149693550.py:40: SettingWithCopyWarning:


A v

time  action  prediction    reward  explore  \
0     [2022-11-08 00:15:18+11:00]       1    0.552324  0.999016  explore   
1     [2022-11-08 00:16:18+11:00]       0    0.580408  0.997792  explore   
2     [2022-11-08 00:17:18+11:00]       1    0.581639  0.999992  explore   
3     [2022-11-08 00:18:18+11:00]       0    0.583330  0.994790  explore   
4     [2022-11-08 00:19:18+11:00]       1    0.578984  0.999428  explore   
...                           ...     ...         ...       ...      ...   
4723  [2022-11-11 13:41:08+11:00]       0    0.078730  0.979570  explore   
4724  [2022-11-11 13:42:08+11:00]       1    0.050431  0.994259  explore   
4725  [2022-11-11 13:43:08+11:00]       1    0.049371  0.981596  explore   
4726  [2022-11-11 13:44:08+11:00]       0    0.078694  0.989640  explore   
4727  [2022-11-11 13:45:08+11:00]       1    0.050024  0.917335  explore   

         score   count                                score_ucb1  
0     0.999016     1.0                   [0, 0.9990158853968117]  
1     0.999016     1.0  [1.7737176171261912, 1.7749411339407435]  
2     0.999504     2.0     [1.9746457400968, 1.6902435304772618]  
3     0.999504     2.0  [1.7722164733996568, 1.7754291357983205]  
4     0.999479     3.0     [1.8323354846506348, 1.6821059082774]  
...        ...     ...                                       ...  
4723  0.991344  2479.0   [1.045775807632689, 1.0457896678850904]  
4724  0.991345  2480.0  [1.0457765233057699, 1.0457805460362355]  
4725  0.991341  2481.0   [1.045777238818452, 1.0457663257538514]  
4726  0.991341  2481.0  [1.0457656950588823, 1.0457670062329674]  
4727  0.991311  2482.0  [1.0457664100917456, 1.0457269040632786]  

[4728 rows x 8 columns]

{0: 1.0457664100917456, 1: 1.0457269040632786}


In [217]:
# the model has the highest "score_ucb1" value is the optimal model at the moment

# Visaulization

In [218]:
# if the optimal model keeps chaning, there is no plot/line
hisplot.astype('double').plot.line()